In [20]:
from tqdm.auto import tqdm
from sentence_transformers import evaluation
import torch 
from transformers import BertModel
from transformers import BertTokenizer
from datasets import Dataset
import pandas as pd
from transformers.optimization import get_linear_schedule_with_warmup
import matplotlib.pyplot as plt 
import numpy as np
import sklearn.model_selection
import sklearn
import random
from spacy.lang.en import English
import re
from sentence_transformers import SentenceTransformer, InputExample, losses, util

In [5]:
#seed setting 
torch.manual_seed(13)
random.seed(13)

In [61]:
#get validation data 
#load data 
df = pd.read_csv("/shared/3/projects/benlitterer/localNews/NetworkMVP/enTrainData.csv", sep="\t")
df = df.loc[(df["url1_lang"] == "en") & (df["url2_lang"] == "en")]

#put ground truth values into a list 
df["ground_truth"] = df['Overall']

#TODO: do we need to make data tensors or does this happen when we call set_format() later on
#df["ground_truth"] = df["ground_truth"].apply(torch.tensor)

#[torch.tensor(gtList) for gtList in df["ground_truth"]]

#get only the columns we need 
#TODO: do we need "pair_id"? 
leanDf = df[["ground_truth",  'text1', 'text2']].dropna().reset_index()

#rescale data from (0, 4): (0, 1)
leanDf["ground_truth"] = (5 - leanDf["ground_truth"]) / 4

#split data 
trainDf, validDf = sklearn.model_selection.train_test_split(leanDf, train_size=.75, test_size=.25, random_state=13)
trainDf = trainDf.reset_index(drop=True)

In [65]:
modelPath = "/home/blitt/projects/localNews/models/sentEmbeddings/0.1-mpNetCosSimChunked/output"
model = SentenceTransformer(modelPath)

In [63]:
nlp = spacy.load("en_core_web_sm", disable=["tok2vec", "tagger", "parser", "attribute_ruler", "lemmatizer", "ner"])
nlp.enable_pipe("senter")
def extractSents(inList): 
    separator = nlp.pipe(inList, n_process=8)
    textList = []
    for text in separator: 
        sentList = [str(sent) for sent in text.sents if len(sent) > 3]
        textList.append(sentList)
    return textList

In [71]:
#get embeddings from trained model for each sentence 
def embedSents(inList): 
    encodedList = [model.encode(item) for item in inList]
    return encodedList

In [72]:
#TODO: apparently we can encode an entire list at once? Faster??
temp = validDf.copy(deep=True) 
temp["text1"] = extractSents(list(temp["text1"]))
temp["text2"] = extractSents(list(temp["text2"]))
temp["vec1"] = temp["text1"].apply(embedSents)
temp["vec2"] = temp["text2"].apply(embedSents)

"""
temp = temp.explode(column="text1")

for i in tqdm(temp["text1"]): 
    model.encode(i)
    
temp = temp.explode(column="text2")
temp.head(10)
"""

'\ntemp = temp.explode(column="text1")\n\nfor i in tqdm(temp["text1"]): \n    model.encode(i)\n    \ntemp = temp.explode(column="text2")\ntemp.head(10)\n'

In [76]:
vecsDf = temp[["index", "vec1", "vec2"]]
vecsDf = vecsDf.explode(column="vec2")
vecsDf = vecsDf.explode(column="vec1")

In [84]:
simList = []
for tup in tqdm(vecsDf.itertuples()): 
    sim = util.cos_sim(tup[2], tup[3])
    simList.append(sim)


0it [00:00, ?it/s]

In [86]:
#TODO: start from here and work on getting CNN up and running for output? 
#TODO: get titles!
vecsDf["cosineSim"] = simList

In [69]:
#temp["text1"].apply(lambda x: model.encode(x)) 
for i in temp["text1"]: 
    model.encod

When a little boy ate cake during a camping trip, his father was furious.
When a little boy ate cake during a camping trip, his father was furious.
When a little boy ate cake during a camping trip, his father was furious.
The dad was camping with his boy on March 28, 2015, and could not believe that the boy had eaten the cake without permission.
The dad was camping with his boy on March 28, 2015, and could not believe that the boy had eaten the cake without permission.
The dad was camping with his boy on March 28, 2015, and could not believe that the boy had eaten the cake without permission.
That’s when Mauricio Alejandro Torres decided to punish the boy for his misdeed in a way that the boy would surely never forget for the rest of his life.
That’s when Mauricio Alejandro Torres decided to punish the boy for his misdeed in a way that the boy would surely never forget for the rest of his life.
That’s when Mauricio Alejandro Torres decided to punish the boy for his misdeed in a way tha

They speak of inequality in relation to nations across the globe, the inequality of transgenders, inequality between races or the sexes, and climate change inequality necessitating wealthy nations to pay a tax to offset natural disasters in poorer nations ostensibly caused by the consumption and emissions of the First World.
They speak of inequality in relation to nations across the globe, the inequality of transgenders, inequality between races or the sexes, and climate change inequality necessitating wealthy nations to pay a tax to offset natural disasters in poorer nations ostensibly caused by the consumption and emissions of the First World.
They speak of inequality in relation to nations across the globe, the inequality of transgenders, inequality between races or the sexes, and climate change inequality necessitating wealthy nations to pay a tax to offset natural disasters in poorer nations ostensibly caused by the consumption and emissions of the First World.
They speak of inequ

He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
He needs an accounting job.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance with tuition for nursing school.
Mom Maria, 42, needs assistance 

"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


"I pulled the car into the snow-filled driveway and parked the car and the engine stopped by itself," he said.


Chiang said there wasn't a single drop of fuel left in the vehicle.


Chiang said there wasn't a

Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address you have provided is already registered.
Try again Thank you, The email address y

...

According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.
According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.
According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.
According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.
According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.
According to TripAdvisor's 'Best Time To Book' report, only two destinations are worth waiting to book - New York and Tokyo.


(Image: PA)

The rest, you should start looking now, so if you plan to fly out in August, booking in at least March should be a priority, but if flights are available, earlier is even better.


(Image: PA)

The rest, you should start looking now, s

This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy HDFC Bank or Kotak Bank.
This is not a recommendation, but if I tell someone that in case you have some extra money, go and buy H

An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An isolated pharma company could do well but broadly there are too many headwinds.
An i

Entire city blocks, even, are set aside in Portland for food carts.
Entire city blocks, even, are set aside in Portland for food carts.
Entire city blocks, even, are set aside in Portland for food carts.


The truth: Portland did have the largest food cart pod in Oregon, and probably the second-, third- and fourth-largest food cart pods, too.


The truth: Portland did have the largest food cart pod in Oregon, and probably the second-, third- and fourth-largest food cart pods, too.


The truth: Portland did have the largest food cart pod in Oregon, and probably the second-, third- and fourth-largest food cart pods, too.


The truth: Portland did have the largest food cart pod in Oregon, and probably the second-, third- and fourth-largest food cart pods, too.


The truth: Portland did have the largest food cart pod in Oregon, and probably the second-, third- and fourth-largest food cart pods, too.
(We're not sure who keeps track of these things.)
(We're not sure who keeps track of these 

KeyboardInterrupt: 

In [ ]:
#util.cos_sim(embed1[i], embed2[i])